In [1]:
import numpy as np
import random

import torch
import torch.nn as nn
import torch.nn.functional as func
import torch.optim as optim

from matplotlib import pyplot as plt

from numpy import exp,arange
from pylab import meshgrid,cm,imshow,contour,clabel,colorbar,axis,title,show

In [2]:
# ==========
# helping methods
# ==========

# generate a list from lower and upper bound
def gen_list(p0, pn, delta, dig=5):
    ret = []
    i = p0
    while i < pn:
        ret.append(float(i))
        i += delta
        i = round(i, dig)
    return ret

# padding and zero padding
def padding(origin, a_list, b_list):
    return np.hstack((a_list, origin, b_list))

def zero_padding(origin, num):
    zero_list = [0 for i in range(num)]
    return padding(origin, zero_list, zero_list)

# trainning pairs
def gen_pair(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-1-length)
        train = current_t[p-length:p+length+1]
        solu = next_t[p]
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

# trainning pairs (in average)
def gen_pair_ave(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-2-length)
        train0 = current_t[p-length:p+length+2]
        solu1 = next_t[p]
        solu2 = next_t[p+1]
        train = []
        for j in range(len(train0)-1):
                train.append(0.5 * (train0[j] + train0[j+1]))
        solu = 0.5 * (solu1 + solu2)
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

In [3]:
# the analytical representation of exact solution
def heat_equ_analytical_solu(x, t):
    return np.sin(np.pi * x) * np.exp(-np.power(np.pi, 2) * t)

In [4]:
# restnet
class ResNet(nn.Module):
    def __init__(self, i, h, o):
        super(ResNet, self).__init__()
        self.linear1 = nn.Linear(i, h)
        self.relu1 = nn.ReLU()
        self.linear2 = nn.Linear(h, o)
        self.relu2 = nn.ReLU()
        
    def forward(self, x):
        out = self.linear1(x)
        out = self.relu1(out)
        out = self.linear2(out)
        out = self.relu2(out)
        return out + torch.mean(x)

    def load_model(self, save_path):
        self.load_state_dict(torch.load(save_path))

    def save_model(self, save_path):
        torch.save(self.state_dict(), save_path)

## $\Delta x=\frac{1}{20}$ $\Delta t=\frac{1}{20}$

In [5]:
x_1 = arange(0, 2 * np.pi, 1/20)
t_1 = arange(0, 2 * np.pi, 1/20)
X_1,T_1 = meshgrid(x_1, t_1) # grid of point
Z_1 = heat_equ_analytical_solu(X_1, T_1) # evaluation of the function on the grid

In [6]:
# preparing the trainning set
data_pairs_1 = gen_pair_ave(Z_1, len(Z_1[0]), len(Z_1), length=3, num=10000)
print(data_pairs_1)

[{'input': [1.2787261901572005e-07, 3.80469208782101e-07, 6.236973839233559e-07, 8.515680595394761e-07, 1.0584703033373767e-06, 1.2393094954055754e-06, 1.3896327746644837e-06], 'solu': 5.198806187282765e-07}, {'input': [-4.731704192628101e-26, -4.9800506096555723e-26, -5.105771652832931e-26, -5.1057716528329305e-26, -4.980050609655572e-26, -4.7317041926281e-26, -4.366847514752236e-26], 'solu': -3.117063511512598e-26}, {'input': [5.279035931147513e-14, 3.22032876139623e-14, 1.0823264098809745e-14, -1.0823264098809766e-14, -3.220328761396244e-14, -5.2790359311475266e-14, -7.207755716158172e-14], 'solu': -6.6075813592535535e-15}, {'input': [-4.647352088919138e-09, -5.441350176883176e-09, -6.101364164686468e-09, -6.611142317488459e-09, -6.958132205310467e-09, -7.1337897855209036e-09, -7.133789785520903e-09], 'solu': -4.036089329577846e-09}, {'input': [-3.210388844207783e-26, -4.3833190083817156e-26, -5.448317311167539e-26, -6.379159959823954e-26, -7.152926519051394e-26, -7.75056428817769e-

In [7]:
model_1 = ResNet(7, 6, 1)
optimizer_1 = optim.Adam(model_1.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_1 = nn.MSELoss()
model_1.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [8]:
list_of_loss_1 = []
list_of_output_1 = []
for data in data_pairs_1:
    output = model_1(torch.FloatTensor(data["input"]))
    loss = criterion_1(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_1.append(np.log10(loss.item()))
    list_of_output_1.append(output)
    model_1.zero_grad()
    loss.backward()
    optimizer_1.step()

<ipython-input-8-ac38450c9edb>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_1.append(np.log10(loss.item()))


In [9]:
list_of_loss_1_file = open('list_of_loss_11.txt', 'w+')
for value in list_of_loss_1:
    list_of_loss_1_file.write(str(value)+" ")
list_of_loss_1_file.close()

list_of_output_1_file = open('list_of_output_11.txt', 'w+')
for value in list_of_output_1:
    list_of_output_1_file.write(str(value)+" ")
list_of_output_1_file.close()

In [10]:
model_1.save_model("model_1 delta x=1 20 delta t=1 20")

## $\Delta x=\frac{1}{40}$ $\Delta t=\frac{1}{20}$

In [11]:
x_2 = arange(0, 2 * np.pi, 1/40)
t_2 = arange(0, 2 * np.pi, 1/20)
X_2,T_2 = meshgrid(x_2, t_2) # grid of point
Z_2 = heat_equ_analytical_solu(X_2, T_2) # evaluation of the function on the grid

In [12]:
# preparing the trainning set
data_pairs_2 = gen_pair_ave(Z_2, len(Z_2[0]), len(Z_2), length=3, num=10000)
print(data_pairs_2)

[{'input': [2.8158876029676326e-10, -2.8158876029675794e-10, -8.430301925452849e-10, -1.3992740633207837e-09, -1.9468909441900608e-09, -2.482504594981471e-09, -3.002812779428279e-09], 'solu': -8.542540524629858e-10}, {'input': [5.1225815524008276e-11, 5.154359895153041e-11, 5.15435989515304e-11, 5.1225815524008276e-11, 5.059220790946841e-11, 4.9646682509550355e-11, 4.839506880276372e-11], 'solu': 3.127325922003715e-11}, {'input': [0.0004786013934440819, 0.0005067285568491565, 0.0005317315701969117, 0.0005534562815957133, 0.0005717687509755878, 0.0005865560758732943, 0.0005977270875135541], 'solu': 0.000337883966985134}, {'input': [6.159589649462352e-08, 4.427034838757978e-08, 2.667185886134193e-08, 8.908928455930814e-09, -8.908928455930649e-09, -2.6671858861341964e-08, -4.427034838758002e-08], 'solu': 5.438883229580035e-09}, {'input': [5.049437616397061e-17, 5.1126758551515e-17, 5.144392747121686e-17, 5.144392747121686e-17, 5.1126758551515e-17, 5.04943761639706e-17, 4.955067915629137e-

In [13]:
model_2 = ResNet(7, 6, 1)
optimizer_2 = optim.Adam(model_2.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_2 = nn.MSELoss()
model_2.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [14]:
list_of_loss_2 = []
list_of_output_2 = []
for data in data_pairs_2:
    output = model_2(torch.FloatTensor(data["input"]))
    loss = criterion_2(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_2.append(np.log10(loss.item()))
    list_of_output_2.append(output)
    model_2.zero_grad()
    loss.backward()
    optimizer_2.step()

<ipython-input-14-de329c128c88>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_2.append(np.log10(loss.item()))


In [15]:
list_of_loss_2_file = open('list_of_loss_21.txt', 'w+')
for value in list_of_loss_2:
    list_of_loss_2_file.write(str(value)+" ")
list_of_loss_2_file.close()

list_of_output_2_file = open('list_of_output_21.txt', 'w+')
for value in list_of_output_2:
    list_of_output_2_file.write(str(value)+" ")
list_of_output_2_file.close()

In [16]:
model_2.save_model("model_1 delta x=1 40 delta t=1 20")

## $\Delta x=\frac{1}{80}$ $\Delta t=\frac{1}{20}$

In [17]:
x_3 = arange(0, 2 * np.pi, 1/80)
t_3 = arange(0, 2 * np.pi, 1/20)
X_3,T_3 = meshgrid(x_3, t_3) # grid of point
Z_3 = heat_equ_analytical_solu(X_3, T_3) # evaluation of the function on the grid

In [18]:
# preparing the trainning set
data_pairs_3 = gen_pair_ave(Z_3, len(Z_3[0]), len(Z_3), length=3, num=10000)
print(data_pairs_3)

[{'input': [-1.7557990938923963e-09, -1.596852992641453e-09, -1.435444659818063e-09, -1.2718229753723417e-09, -1.106240232082168e-09, -9.389517465360113e-10, -7.702154654532764e-10], 'solu': -7.764454149524871e-10}, {'input': [3.274307798074756e-11, 3.428420495041104e-11, 3.5772468161009736e-11, 3.7205572818544365e-11, 3.8581309179506514e-11, 3.989755595814294e-11, 4.115228359732444e-11], 'solu': 2.2713928734604217e-11}, {'input': [1.2191796877383264e-14, 1.2765631352793344e-14, 1.3319782149928846e-14, 1.3853394808426252e-14, 1.436564653624314e-14, 1.4855747478343968e-14, 1.532294193459924e-14], 'solu': 8.457470173771694e-15}, {'input': [-8.314542625767568e-20, -5.948133440545625e-20, -3.5725526646876193e-20, -1.1914632715644476e-20, 1.191463271564442e-20, 3.572552664687614e-20, 5.948133440545673e-20], 'solu': -7.273859744668234e-21}, {'input': [5.525348380353782e-18, 5.115251979387246e-18, 4.697268230629364e-18, 4.272041634724644e-18, 3.840227860262915e-18, 3.4024927327859367e-18, 2.9

In [19]:
model_3 = ResNet(7, 6, 1)
optimizer_3 = optim.Adam(model_3.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_3 = nn.MSELoss()
model_3.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [20]:
list_of_loss_3 = []
list_of_output_3 = []
for data in data_pairs_3:
    output = model_3(torch.FloatTensor(data["input"]))
    loss = criterion_3(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_3.append(np.log10(loss.item()))
    list_of_output_3.append(output)
    model_3.zero_grad()
    loss.backward()
    optimizer_3.step()

<ipython-input-20-3f959fb14d49>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_3.append(np.log10(loss.item()))


In [21]:
list_of_loss_3_file = open('list_of_loss_31.txt', 'w+')
for value in list_of_loss_3:
    list_of_loss_3_file.write(str(value)+" ")
list_of_loss_3_file.close()

list_of_output_3_file = open('list_of_output_31.txt', 'w+')
for value in list_of_output_3:
    list_of_output_3_file.write(str(value)+" ")
list_of_output_3_file.close()

In [22]:
model_3.save_model("model_1 delta x=1 80 delta t=1 20")

## $\Delta x=\frac{1}{160}$ $\Delta t=\frac{1}{20}$

In [23]:
x_4 = arange(0, 2 * np.pi, 1/160)
t_4 = arange(0, 2 * np.pi, 1/20)
X_4,T_4 = meshgrid(x_4, t_4) # grid of point
Z_4 = heat_equ_analytical_solu(X_4, T_4) # evaluation of the function on the grid

In [24]:
# preparing the trainning set
data_pairs_4 = gen_pair_ave(Z_4, len(Z_4[0]), len(Z_4), length=3, num=10000)
print(data_pairs_4)

[{'input': [-1.3517560248342365e-19, -1.357045991041439e-19, -1.3618127901865434e-19, -1.366054584577739e-19, -1.3697697389225423e-19, -1.3729568209582312e-19, -1.3756146020040127e-19], 'solu': -8.339736262899949e-20}, {'input': [-5.072523016471665e-11, -5.052749570678722e-11, -5.0310281937427955e-11, -5.007367259668181e-11, -4.981775890195371e-11, -4.9542639512844505e-11, -4.924842049311587e-11], 'solu': -3.056987823808039e-11}, {'input': [0.0005512675475064844, 0.0005814107108863641, 0.0006113297293695382, 0.0006410130686048469, 0.0006704492850999669, 0.0006996270306330938, 0.0007285350566279035], 'solu': 0.00039133721255282767}, {'input': [-1.4637983214621361e-06, -1.4778061570732834e-06, -1.4912442702795527e-06, -1.5041074804324962e-06, -1.5163908285197388e-06, -1.5280895790767677e-06, -1.5391992220125475e-06], 'solu': -9.182546465915517e-07}, {'input': [-1.2496196801288968e-16, -1.2609828285675325e-16, -1.2718598441218497e-16, -1.2822465334953e-16, -1.292138892421409e-16, -1.30153

In [25]:
model_4 = ResNet(7, 6, 1)
optimizer_4 = optim.Adam(model_4.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_4 = nn.MSELoss()
model_4.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [26]:
list_of_loss_4 = []
list_of_output_4 = []
for data in data_pairs_4:
    output = model_4(torch.FloatTensor(data["input"]))
    loss = criterion_4(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_4.append(np.log10(loss.item()))
    list_of_output_4.append(output)
    model_4.zero_grad()
    loss.backward()
    optimizer_4.step()

<ipython-input-26-f52da78e2a74>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_4.append(np.log10(loss.item()))


In [27]:
list_of_loss_4_file = open('list_of_loss_41.txt', 'w+')
for value in list_of_loss_4:
    list_of_loss_4_file.write(str(value)+" ")
list_of_loss_4_file.close()

list_of_output_4_file = open('list_of_output_41.txt', 'w+')
for value in list_of_output_4:
    list_of_output_4_file.write(str(value)+" ")
list_of_output_4_file.close()

In [28]:
model_4.save_model("model_1 delta x=1 160 delta x=1 20")